In [1]:
# Install required packages (Colab)
!pip install bokeh --quiet

# Imports
import numpy as np
import pandas as pd
import math
from datetime import datetime, timedelta
from bokeh.plotting import figure, show, output_notebook, ColumnDataSource
from bokeh.layouts import column, row
from bokeh.models import HoverTool, Legend
from bokeh.io import output_file, save
from google.colab import files

# Prepare Bokeh for notebook
output_notebook()


In [ ]:
import pandas as pd
import numpy as np
from haversine import haversine
import pathway as pw
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColumnDataSource, Select, Slider, CustomJS
from bokeh.layouts import column, row

output_notebook()

In [ ]:
df = pd.read_csv('dataset.csv')
print("Available columns:")
for col in df.columns:
    print(" -", col)

Available columns:
 - ID
 - SystemCodeNumber
 - Capacity
 - Latitude
 - Longitude
 - Occupancy
 - VehicleType
 - TrafficConditionNearby
 - QueueLength
 - IsSpecialDay
 - LastUpdatedDate
 - LastUpdatedTime


In [ ]:
# Based on your dataset, set the following:
timestamp_date_col = 'LastUpdatedDate'      # e.g., 'LastUpdatedDate'
timestamp_time_col = 'LastUpdatedTime'      # e.g., 'LastUpdatedTime'
lot_id_col         = 'SystemCodeNumber'     # e.g., 'SystemCodeNumber'
occ_col            = 'Occupancy'            # e.g., 'Occupancy'
cap_col            = 'Capacity'             # e.g., 'Capacity'
queue_col          = 'QueueLength'          # e.g., 'QueueLength'
traffic_col        = 'TrafficConditionNearby'  # e.g., 'TrafficConditionNearby'
special_col        = 'IsSpecialDay'         # e.g., 'IsSpecialDay'
vehtype_col        = 'VehicleType'          # e.g., 'VehicleType'
df['timestamp'] = pd.to_datetime(df[timestamp_date_col] + ' ' + df[timestamp_time_col], format='%d-%m-%Y %H:%M:%S', errors='coerce')
df[[timestamp_date_col, timestamp_time_col, 'timestamp', lot_id_col, occ_col, cap_col]].head()

LastUpdatedDate LastUpdatedTime           timestamp SystemCodeNumber  \
0      04-10-2016        07:59:00 2016-10-04 07:59:00      BHMBCCMKT01   
1      04-10-2016        08:25:00 2016-10-04 08:25:00      BHMBCCMKT01   
2      04-10-2016        08:59:00 2016-10-04 08:59:00      BHMBCCMKT01   
3      04-10-2016        09:32:00 2016-10-04 09:32:00      BHMBCCMKT01   
4      04-10-2016        09:59:00 2016-10-04 09:59:00      BHMBCCMKT01   

   Occupancy  Capacity  
0         61       577  
1         64       577  
2         80       577  
3        107       577  
4        150       577

In [ ]:
df['timestamp'] = pd.to_datetime(df[timestamp_date_col] + ' ' + df[timestamp_time_col], format='%d-%m-%Y %H:%M:%S', errors='coerce')
df[[timestamp_date_col, timestamp_time_col, 'timestamp', lot_id_col, occ_col, cap_col]].head()

LastUpdatedDate LastUpdatedTime           timestamp SystemCodeNumber  \
0      04-10-2016        07:59:00 2016-10-04 07:59:00      BHMBCCMKT01   
1      04-10-2016        08:25:00 2016-10-04 08:25:00      BHMBCCMKT01   
2      04-10-2016        08:59:00 2016-10-04 08:59:00      BHMBCCMKT01   
3      04-10-2016        09:32:00 2016-10-04 09:32:00      BHMBCCMKT01   
4      04-10-2016        09:59:00 2016-10-04 09:59:00      BHMBCCMKT01   

   Occupancy  Capacity  
0         61       577  
1         64       577  
2         80       577  
3        107       577  
4        150       577

In [ ]:
first_lot = df[lot_id_col].unique()[0]
lot1 = df[df[lot_id_col] == first_lot].copy()
lot1['occ_rate'] = lot1[occ_col] / lot1[cap_col]

p = figure(x_axis_type='datetime', title=f"Lot {first_lot} Occupancy Rate")
p.line(lot1['timestamp'], lot1['occ_rate'], legend_label='Occupancy Rate')
show(p)

In [ ]:
# Create a ColumnDataSource
source = ColumnDataSource(data=dict(timestamp=[], occ_rate=[]))

# Get unique parking lot IDs
lot_ids = df[lot_id_col].unique().tolist()

# Create a Select widget for choosing the parking lot
lot_select = Select(title="Select Parking Lot:", value=lot_ids[0], options=lot_ids)

# Create the figure
p = figure(x_axis_type='datetime', title=f"Lot {lot_select.value} Occupancy Rate")
line = p.line(x='timestamp', y='occ_rate', source=source)

# Add a CustomJS callback to update the plot when the select widget changes
callback = CustomJS(args=dict(source=source, df=df, lot_select=lot_select, lot_id_col=lot_id_col, occ_col=occ_col, cap_col=cap_col, line=line), code="""
    const current_lot_id = lot_select.value;
    const lot_data = df.filter(row => row[lot_id_col] === current_lot_id);
    const timestamps = lot_data.map(row => new Date(row.timestamp));
    const occ_rates = lot_data.map(row => row[occ_col] / row[cap_col]);
    source.data = { timestamp: timestamps, occ_rate: occ_rates };
    p.title.text = "Lot " + current_lot_id + " Occupancy Rate"; // Update the title
""")

lot_select.js_on_change('value', callback)

# Initial data load for the first lot
first_lot_data = df[df[lot_id_col] == lot_ids[0]].copy()
first_lot_data['occ_rate'] = first_lot_data[occ_col] / first_lot_data[cap_col]
source.data = {
    'timestamp': first_lot_data['timestamp'],
    'occ_rate': first_lot_data['occ_rate']
}


# Arrange the layout
layout = column(lot_select, p)

# Show the plot
show(layout)

In [ ]:
# -----------------------------
# 4. MODEL 1: BASELINE LINEAR
# -----------------------------
def baseline_price_update(prices, occ, cap, alpha=5):
    """
    prices: pandas Series of previous prices indexed by lot ID
    occ, cap: numpy arrays of occupancy and capacity
    """
    delta = alpha * (occ / cap)
    return prices + delta

# Initialize price Series
lots = df[lot_id_col].unique()
base_price = 10
prices = pd.Series(base_price, index=lots)

# Update prices at the first timestamp
time0 = df[df['timestamp'] == df['timestamp'].min()]
prices = baseline_price_update(
    prices,
    time0[occ_col].values,
    time0[cap_col].values
)
print("Baseline model prices (first timestamp):")
print(prices.head())

Baseline model prices (first timestamp):
BHMBCCMKT01    10.528596
BHMBCCTHL01    11.550388
BHMEURBRD01    11.244681
BHMMBMMBX01    11.921397
BHMNCPHST01    10.987500
dtype: float64


EXPERIMENTATION CELLS


In [ ]:
import pandas as pd
import numpy as np
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import ColumnDataSource, Select, CustomJS
from bokeh.layouts import column
from haversine import haversine

output_notebook()

# COLUMN MAPPINGS
timestamp_date_col = 'LastUpdatedDate'
timestamp_time_col = 'LastUpdatedTime'
lot_id_col         = 'SystemCodeNumber'
occ_col            = 'Occupancy'
cap_col            = 'Capacity'
queue_col          = 'QueueLength'
traffic_col        = 'TrafficConditionNearby'
special_col        = 'IsSpecialDay'
vehtype_col        = 'VehicleType'

# Timestamp creation
df['timestamp'] = pd.to_datetime(
    df[timestamp_date_col] + ' ' + df[timestamp_time_col],
    format='%d-%m-%Y %H:%M:%S',
    errors='coerce'
)

# Fix: Convert traffic level to numeric
traffic_map = {'Low': 1, 'Medium': 2, 'High': 3}
df[traffic_col] = df[traffic_col].map(traffic_map)

# Define pricing models
def baseline_price_update(prices, occ, cap, alpha=5):
    return prices + alpha * (occ / cap)

type_weights = {'car': 1.0, 'bike': 0.5, 'truck': 1.5}

def demand_price_update(features, base_price=10, coeffs=None, lam=0.5):
    if coeffs is None:
        coeffs = {'alpha': 2, 'beta': 0.1, 'gamma': 0.05, 'delta': 0.2, 'epsilon': 0.5}
    demand = (
        coeffs['alpha'] * (features[occ_col] / features[cap_col]) +
        coeffs['beta'] * features[queue_col] -
        coeffs['gamma'] * features[traffic_col] +
        coeffs['delta'] * features[special_col] +
        coeffs['epsilon'] * type_weights.get(str(features[vehtype_col]).lower(), 1)
    )
    norm = np.tanh(demand)
    return float(np.clip(base_price * (1 + lam * norm), 0.5 * base_price, 2 * base_price))


In [ ]:
df = df.sort_values('timestamp')
lots = df[lot_id_col].unique()
base_price = 10
current_prices_baseline = pd.Series(base_price, index=lots, dtype=float)

# Model 1: Baseline Pricing
df['price_baseline'] = np.nan
for ts, group in df.groupby('timestamp'):
    idx = group.index
    occ = group[occ_col].values
    cap = group[cap_col].values
    updated = baseline_price_update(
        current_prices_baseline.loc[group[lot_id_col]].values, occ, cap
    )
    df.loc[idx, 'price_baseline'] = updated
    current_prices_baseline.loc[group[lot_id_col]] = updated

# Model 2: Demand-Based Pricing
df['price_demand'] = df.apply(lambda row: demand_price_update(row), axis=1)

# Model 3: Competitor-Based Pricing
coords = df.groupby(lot_id_col)[['Latitude', 'Longitude']].first().to_dict('index')

def find_nearest(lot, k=3):
    base = coords[lot]
    dists = []
    for other, c in coords.items():
        if other == lot: continue
        d = haversine((base['Latitude'], base['Longitude']), (c['Latitude'], c['Longitude']))
        dists.append((other, d))
    dists.sort(key=lambda x: x[1])
    return [l for l, _ in dists[:k]]

nearest_map = {lot: find_nearest(lot, k=3) for lot in coords}
df['price_competitor'] = np.nan

for ts, group in df.groupby('timestamp'):
    pdemand = group['price_demand']
    idxs = group.index
    comp_prices = []
    for lot, own_price in zip(group[lot_id_col], pdemand):
        neighbors = nearest_map[lot]
        neighbor_prices = df.loc[
            (df['timestamp'] == ts) & (df[lot_id_col].isin(neighbors)),
            'price_demand'
        ]
        avg_comp = neighbor_prices.mean()
        occ_rate = group.loc[group[lot_id_col]==lot, occ_col].iloc[0] / \
                   group.loc[group[lot_id_col]==lot, cap_col].iloc[0]
        if occ_rate > 0.9 and avg_comp < own_price:
            new_p = avg_comp * 0.95
        else:
            new_p = min(own_price * 1.05, avg_comp * 1.05)
        comp_prices.append(new_p)
    df.loc[idxs, 'price_competitor'] = comp_prices


In [ ]:
# BOKEH VISUALIZATION
full_source = ColumnDataSource(df)
plot_source = ColumnDataSource(data=dict(
    timestamp=[], baseline=[], demand=[], competitor=[]
))

lot_ids = [str(l) for l in df[lot_id_col].unique()]
lot_select = Select(title="Select Lot:", value=lot_ids[0], options=lot_ids)

p = figure(x_axis_type='datetime', width=700, height=350,
           title=f"Lot {lot_select.value} Pricing Comparison")
p.line('timestamp','baseline',   source=plot_source, legend_label='Baseline')
p.line('timestamp','demand',     source=plot_source, legend_label='Demand‑Based', line_dash='dashed')
p.line('timestamp','competitor', source=plot_source, legend_label='Competitor‑Based', line_dash='dotdash')
p.legend.location = 'top_left'

callback = CustomJS(args=dict(
    full_source=full_source,
    plot_source=plot_source,
    lot_select=lot_select,
    lot_id_col=lot_id_col
), code="""
    const data = full_source.data;
    const sel = lot_select.value;
    const ts = [], b = [], d = [], c = [];
    for (let i = 0; i < data[lot_id_col].length; i++) {
        if (String(data[lot_id_col][i]) === sel) {
            ts.push(new Date(data['timestamp'][i]));
            b.push(data['price_baseline'][i]);
            d.push(data['price_demand'][i]);
            c.push(data['price_competitor'][i]);
        }
    }
    plot_source.data = {
        timestamp: ts,
        baseline: b,
        demand: d,
        competitor: c
    };
    plot_source.change.emit();
    p.title.text = "Lot " + sel + " Pricing Comparison";
""")
lot_select.js_on_change('value', callback)

initial = df[df[lot_id_col] == lot_ids[0]].copy()
plot_source.data = {
    'timestamp':    initial['timestamp'],
    'baseline':     initial['price_baseline'],
    'demand':       initial['price_demand'],
    'competitor':   initial['price_competitor'],
}

show(column(lot_select, p))
